In [1]:
from agents import Agent, Runner, WebSearchTool, function_tool
# from agents import Agent, Runner, InputGuardrail, GuardrailFunctionOutput, ModelSettings, function_tool, 
import os
from dotenv import load_dotenv
import pandas as pd
# from pydantic import BaseModel
# import asyncio
from langchain_community.document_loaders.csv_loader import CSVLoader, UnstructuredCSVLoader
from langchain_experimental.tools import PythonAstREPLTool
from langchain_experimental.agents import create_pandas_dataframe_agent
from langchain_openai import ChatOpenAI
# from crewai_tools import SerperDevTool, FileReadTool


In [33]:
# load_dotenv()
# OPENAI_API_KEY = os.getenv("OPENAI_API_KEY")
# SERPER_API_KEY = os.getenv("SERPER_API_KEY")

In [5]:
# Tools
# https://python.langchain.com/docs/integrations/document_loaders/

# loader = CSVLoader()
# data = loader.load()
event_loader = CSVLoader(file_path="data/event_data_sherdog.csv")
event_data = event_loader.load()
print(event_data)
fighter_loader = CSVLoader(file_path="data/fighter_info.csv")
fighter_data = fighter_loader.load()
print(fighter_data)
# loader = UnstructuredCSVLoader(file_path="example_data/mlb_teams_2012.csv", mode="elements")
# docs = loader.load()

# search_tool = SerperDevTool()

[Document(metadata={'source': 'data/event_data_sherdog.csv', 'row': 0}, page_content='Event Name: UFC on ESPN 59 - Namajunas vs. Cortez\nEvent Location: Ball Arena, Denver, Colorado, United States\nEvent Date: 2024-07-13T00:00:00+00:00\nFighter 1: Rose Namajunas\nFighter 2: Tracy Cortez\nFighter 1 ID: 69083\nFighter 2 ID: 160955\nWeight Class: Flyweight\nWinning Fighter: Rose Namajunas\nWinning Method: Decision (Unanimous)\nWinning Round: 5\nWinning Time: 5:00\nReferee: Herb Dean\nFight Type: Main Event'), Document(metadata={'source': 'data/event_data_sherdog.csv', 'row': 1}, page_content='Event Name: UFC on ESPN 59 - Namajunas vs. Cortez\nEvent Location: Ball Arena, Denver, Colorado, United States\nEvent Date: 2024-07-13T00:00:00+00:00\nFighter 1: Muslim Salikhov\nFighter 2: Santiago Ponzinibbio\nFighter 1 ID: 129929\nFighter 2 ID: 64593\nWeight Class: Welterweight\nWinning Fighter: Muslim Salikhov\nWinning Method: Decision (Split)\nWinning Round: 3\nWinning Time: 5:00\nReferee: Dan M

In [2]:
# Create Function Tools to Query the Data
# - tools that can analyze and query your dataframes

# @function_tool
# def analyze_fighter(fighter_name: str) -> str:
#     """Search for a fighter by name and return their information"""
#     matches = fighter_df[fighter_df['name'].str.contains(fighter_name, case=False, na=False)]
#     if matches.empty:
#         return f"No fighter found with name '{fighter_name}'"
#     return matches.to_string()

# @function_tool
# def analyze_events(event_name: str = None) -> str:
#     """Search for events by name"""
#     if event_name:
#         matches = event_df[event_df['event_name'].str.contains(event_name, case=False, na=False)]
#         if matches.empty:
#             return f"No events found matching '{event_name}'"
#         return matches.to_string()
#     return f"Found {len(event_df)} total events in database"

# @function_tool
# def run_fighter_analysis(query: str) -> str:
#     """Run a pandas dataframe analysis on fighter data"""
#     llm = ChatOpenAI(temperature=0, model="gpt-4o")
#     pandas_agent = create_pandas_dataframe_agent(llm, fighter_df, verbose=True)
#     return pandas_agent.invoke({"input": query})["output"]

# @function_tool
# def run_event_analysis(query: str) -> str:
#     """Run a pandas dataframe analysis on event data"""
#     llm = ChatOpenAI(temperature=0, model="gpt-4o")
#     pandas_agent = create_pandas_dataframe_agent(llm, event_df, verbose=True)
#     return pandas_agent.invoke({"input": query})["output"]

# Load your data
event_df = pd.read_csv("data/event_data_sherdog.csv")
fighter_df = pd.read_csv("data/fighter_info.csv")

# Create a single function tool that handles all fighter data queries
@function_tool
def fight_data_query(query: str) -> str:
    """Query UFC fighter and event data using natural language. Ask any question about fighters, events, statistics, etc."""
    llm = ChatOpenAI(temperature=0.3, model="o3-mini")
    # Create a dictionary of dataframes that the agent can access
    dfs = {"events": event_df, "fighters": fighter_df}
    # Let the agent know about all available dataframes
    agent = create_pandas_dataframe_agent(llm, dfs, verbose=True)
    return agent.invoke({"input": query})["output"]

In [4]:
# Agents
history_tutor_agent = Agent(
    name="History Tutor",
    handoff_description="Specialist agent for historical questions",
    instructions="You provide assistance with historical queries. Explain important events and context clearly. At the beginning of your response, print your name 'History Tutor'.",
    model="o3-mini"
)

math_tutor_agent = Agent(
    name="Math Tutor",
    handoff_description="Specialist agent for math questions",
    instructions="You provide help with math problems. Explain your reasoning at each step and include examples. At the beginning of your response, print your name 'Math Tutor'.",
    model="o3-mini"
)

web_search_agent = Agent(
    name="Web Search Agent",
    handoff_description="Specialist agent for web search upcoming or unknown information",
    instructions="You search the web for information. At the beginning of your response, print your name 'Web Search'.",
    # model="gpt-4o-mini-search-preview",
    tools=[WebSearchTool(search_context_size="low")]
)

fight_analyst_agent = Agent(
    name="Fight Analyst",
    handoff_description="Specialist agent for UFC/MMA fight analysis using CSV data",
    instructions="""You are a UFC/MMA fight analyst who can answer questions about fighters and events.
    You have access to CSV data about fighters and events. At the beginning of your response, print your name 'Fight Analyst'.
    When asked complex questions, you can use pandas analysis tools to calculate statistics and provide insights.
    Always explain your reasoning and cite statistics where applicable.""",
    model="o3-mini",  # Need a more powerful model for data analysis
    tools=[fight_data_query]
    # tools=[analyze_fighter, analyze_events, run_fighter_analysis, run_event_analysis]
)
# fight_analyst_agent = Agent(
#     name="Fight Analyst",
#     handoff_description="Specialist agent for UFC/MMA fight analysis using CSV data",
#     instructions="""You are a UFC/MMA fight analyst who can answer questions about fighters and events.
#     You have access to fighter_df and event_df dataframes.
#     When asked questions, write Python code that answers the question and create visualizations when appropriate.
#     At the beginning of your response, print your name 'Fight Analyst'.
#     Always use the execute_python_code tool to run your analysis.""",
#     model="gpt-4o",
#     tools=[execute_python_code]
# )

# Define your handoffs
triage_agent = Agent(
    name="Triage Agent",
    instructions="You determine which agent to use based on the user's homework question. Print which agent you decide:",
    model="gpt-4o-mini",
    handoffs=[history_tutor_agent, math_tutor_agent, web_search_agent, fight_analyst_agent]
)

In [5]:
# Single Question (jupyter notebook)

import nest_asyncio
nest_asyncio.apply()

# result = Runner.run_sync(triage_agent, "What is the capital of France?")
# print(result.final_output)

# result = Runner.run_sync(triage_agent, "What is 4+9?")
# print(result.final_output)

# result = Runner.run_sync(triage_agent, "What is the upcoming UFC event and main event?")
# print(result.final_output)

# result = Runner.run_sync(triage_agent, "What is the weather in Miami?")
# print(result.final_output)

result = Runner.run_sync(triage_agent, "Tell me about Max Holloways most recent 3 fights and outcomes in your dataset")
print(result.final_output)

result = Runner.run_sync(triage_agent, "List the most recent 3 events in your dataset")
print(result.final_output)

Fight Analyst

Based on our records, here are details on Max Holloway’s three most recent bouts along with their outcomes:

1. UFC 276 – On July 2, 2022, Holloway faced Calvin Kattar. He won the fight via a unanimous decision.
2. UFC 245 – On December 14, 2019, he squared off against Alexander Volkanovski in a title bout. In a hard-fought contest, Holloway lost by unanimous decision.
3. UFC 212 – On June 4, 2017, Holloway fought Jose Aldo (in a bout that was pivotal for his ascent in the division). Holloway secured a victory via unanimous decision.

These events reflect Holloway’s high-level competition and his willingness to face elite opponents in title-relevant matchups. Note that details such as event dates, the method of victory/defeat, and the level of competition help put these results in context. If you’d like more information (like fight statistics or additional background on any of the events), please let me know!


Error getting response: Error code: 400 - {'error': {'message': "The requested model 'gpt-4o-mini-search-preview' does not exist.", 'type': 'invalid_request_error', 'param': 'model', 'code': 'model_not_found'}}. (request_id: req_cc61c59f23fb8ad8e9c91c65944abf0f)


BadRequestError: Error code: 400 - {'error': {'message': "The requested model 'gpt-4o-mini-search-preview' does not exist.", 'type': 'invalid_request_error', 'param': 'model', 'code': 'model_not_found'}}

In [ ]:
# Single Question

result = Runner.run_sync(triage_agent, "What is the capital of France?")
print(result.final_output)
result = Runner.run_sync(triage_agent, "What is 4+9?")
print(result.final_output)

In [ ]:
# Multiple Questions

async def main():
    result = await Runner.run(triage_agent, "What is the capital of France?")
    print(result.final_output)
    
    result = await Runner.run(triage_agent, "what is 4+9")
    print(result.final_output)

    result = await Runner.run(triage_agent, "what is life")
    print(result.final_output)
    
if __name__ == "__main__":
    asyncio.run(main())